In [8]:
import pandas as pd
import numpy as np
import os
from math import sqrt
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
import tensorflow as tf
import keras

Using TensorFlow backend.


In [2]:
train = pd.read_csv(os.path.join('data', 'clean_train.csv'))
test = pd.read_csv(os.path.join('data', 'clean_test.csv'))

In [3]:
train.head()

Unnamed: 0      PCA0      PCA1      PCA2      PCA3      PCA4      PCA5  \
0           0  4.345109  1.619386 -0.739617 -2.080179 -0.985088  1.999117   
1           1  0.019142 -3.106959  0.168223 -0.553341  0.940712  0.200719   
2           2  4.851149  1.242811 -0.351815 -1.484957 -0.758200  2.181179   
3           3 -1.771641  0.039500 -1.358623  1.920760 -2.550817  0.209519   
4           4  6.463747  1.064473  0.209472  0.448906 -1.555301  3.215822   

       PCA6      PCA7      PCA8  ...    PCA164    PCA165    PCA166    PCA167  \
0 -1.231870 -0.131782  1.316470  ...  0.160733  0.071333  0.155468  0.172801   
1 -0.468954  0.235082 -0.838022  ... -1.063234 -0.334556  0.361166 -1.218397   
2 -1.843949  0.296194  1.299142  ...  0.088334  0.238624  0.327280  0.325285   
3 -0.756387  0.700109 -1.408543  ... -0.172186 -0.518922  0.231498 -0.074296   
4 -0.946356 -0.805204  2.112526  ... -0.270189  0.375297 -0.396732 -0.109084   

     PCA168    PCA169    PCA170    PCA171  Id  SalePrice  
0 -0.169568 -0.144326  0.391713 -0.013357   1     208500  
1 -0.346191 -0.962753 -0.138863  1.083103   2     181500  
2 -0.704900 -0.036388 -0.540516  0.021711   3     223500  
3 -0.034287 -0.877735  0.028065 -0.321009   4     140000  
4  0.317305 -0.145975 -0.674692 -0.378458   5     250000  

[5 rows x 175 columns]

In [4]:
test.head()

Unnamed: 0      PCA0      PCA1      PCA2      PCA3      PCA4      PCA5  \
0           0 -3.208086 -2.987338 -0.327066 -1.609206  0.016879 -1.514939   
1           1 -1.403753 -4.261851  0.107527  0.935981  0.165777 -0.299485   
2           2  2.257002  0.427951 -0.610464 -1.301125 -1.058327  2.674177   
3           3  3.253618  0.537318 -0.796079 -0.851716 -1.209643  2.388795   
4           4  2.876409 -0.075909 -0.154959 -2.469870  1.407820  0.487532   

       PCA6      PCA7      PCA8  ...    PCA163    PCA164    PCA165    PCA166  \
0 -0.417889 -0.988173 -0.653363  ... -0.027364  0.653222 -0.201973 -0.769946   
1 -0.524918 -2.332121  0.031044  ...  3.856117  0.787996  0.215221  0.458275   
2 -1.500824 -0.223999  0.403440  ... -0.117138 -0.378473 -0.031613  0.090593   
3 -1.340676 -0.876322  0.421183  ... -0.441586  0.020066 -0.151709  0.444826   
4  0.072190  2.414446  1.667224  ...  0.269062  0.651172 -0.050461 -0.526448   

     PCA167    PCA168    PCA169    PCA170    PCA171    Id  
0 -0.344834  0.514257  1.114106  0.337765 -0.639617  1461  
1  1.135109  0.378972  0.953559 -1.008240  4.445435  1462  
2 -0.173914 -0.150098 -0.006612  0.190780 -0.152486  1463  
3  0.008218 -0.161705 -0.453482  0.472352  0.046141  1464  
4 -0.843701  0.574770 -0.227828  1.071423  1.362638  1465  

[5 rows x 174 columns]

In [5]:
# Set aside unnecessary features

trainId = train['Id'].astype(int)
testId = test['Id'].astype(int)

train = train.drop('Id', axis=1)
test = test.drop('Id', axis=1)

In [6]:
X = train.drop('SalePrice', axis=1)
y = train['SalePrice']
X_test = test

In [7]:
print(y)
print(X.shape)
print(X_test.shape)
X.head()

0       208500
1       181500
2       223500
3       140000
4       250000
         ...  
1455    175000
1456    210000
1457    266500
1458    142125
1459    147500
Name: SalePrice, Length: 1460, dtype: int64
(1460, 173)
(1459, 173)


Unnamed: 0      PCA0      PCA1      PCA2      PCA3      PCA4      PCA5  \
0           0  4.345109  1.619386 -0.739617 -2.080179 -0.985088  1.999117   
1           1  0.019142 -3.106959  0.168223 -0.553341  0.940712  0.200719   
2           2  4.851149  1.242811 -0.351815 -1.484957 -0.758200  2.181179   
3           3 -1.771641  0.039500 -1.358623  1.920760 -2.550817  0.209519   
4           4  6.463747  1.064473  0.209472  0.448906 -1.555301  3.215822   

       PCA6      PCA7      PCA8  ...    PCA162    PCA163    PCA164    PCA165  \
0 -1.231870 -0.131782  1.316470  ... -0.276936 -0.128260  0.160733  0.071333   
1 -0.468954  0.235082 -0.838022  ...  0.140974 -0.224535 -1.063234 -0.334556   
2 -1.843949  0.296194  1.299142  ... -0.289024 -0.282563  0.088334  0.238624   
3 -0.756387  0.700109 -1.408543  ...  0.286790  0.672251 -0.172186 -0.518922   
4 -0.946356 -0.805204  2.112526  ... -0.235585  0.019570 -0.270189  0.375297   

     PCA166    PCA167    PCA168    PCA169    PCA170    PCA171  
0  0.155468  0.172801 -0.169568 -0.144326  0.391713 -0.013357  
1  0.361166 -1.218397 -0.346191 -0.962753 -0.138863  1.083103  
2  0.327280  0.325285 -0.704900 -0.036388 -0.540516  0.021711  
3  0.231498 -0.074296 -0.034287 -0.877735  0.028065 -0.321009  
4 -0.396732 -0.109084  0.317305 -0.145975 -0.674692 -0.378458  

[5 rows x 173 columns]

In [30]:
# Setup our model

model = tf.keras.models.Sequential([
    # Flatten out our input
    tf.keras.layers.Flatten(),
    
    # Setup our hidden layer
    
    tf.keras.layers.Dense(1024, activation=tf.nn.relu),
    tf.keras.layers.Dense(1024, activation=tf.nn.relu),
    tf.keras.layers.Dense(2048, activation=tf.nn.relu),
    tf.keras.layers.Dense(2048, activation=tf.nn.relu),
    tf.keras.layers.Dense(1024, activation=tf.nn.relu),
    tf.keras.layers.Dense(1024, activation=tf.nn.relu),
    tf.keras.layers.Dense(512, activation=tf.nn.relu),
    tf.keras.layers.Dense(256, activation=tf.nn.relu),
    tf.keras.layers.Dense(128, activation=tf.nn.relu),
    tf.keras.layers.Dense(64, activation=tf.nn.relu),
    tf.keras.layers.Dense(32, activation=tf.nn.relu),
    
    # Setup output layer
    tf.keras.layers.Dense(1, activation=tf.nn.relu)
])

# Compile our model
model.compile(optimizer='adam', 
              loss = 'mean_squared_error', 
             metrics=['mse'])

# Fit model
history = model.fit(
    X.values,
    y.values,
    epochs=20
)

# Model summary
print(model.summary())

Train on 1460 samples
Epoch 1/20
1460/1460 [==============================] - 8s 5ms/sample - loss: 21378772287.8247 - mse: 21378768896.0000
Epoch 2/20
1460/1460 [==============================] - 7s 4ms/sample - loss: 14424159683.6822 - mse: 14424160256.0000
Epoch 3/20
1460/1460 [==============================] - 7s 4ms/sample - loss: 9813772273.9726 - mse: 9813772288.0000
Epoch 4/20
1460/1460 [==============================] - 6s 4ms/sample - loss: 4094837492.7781 - mse: 4094837504.0000
Epoch 5/20
1460/1460 [==============================] - 7s 5ms/sample - loss: 2989677719.4959 - mse: 2989677568.0000 3s - loss: 3902894729.6
Epoch 6/20
1460/1460 [==============================] - 6s 4ms/sample - loss: 1279209371.7041 - mse: 1279209088.0000
Epoch 7/20
1460/1460 [==============================] - 6s 4ms/sample - loss: 1186372414.0712 - mse: 1186372224.0000
Epoch 8/20
1460/1460 [==============================] - 6s 4ms/sample - loss: 929078176.2630 - mse: 929078208.0000
Epoch 9/20
1460/

In [31]:
mse = mean_squared_error(y.values, model.predict(X.values))
mae = mean_absolute_error(y.values, model.predict(X.values))

In [32]:
print("Training mse = ",mse," & mae = ",mae," & rmse = ", sqrt(mse))

Training mse =  206305033.33630806  & mae =  9953.949831442636  & rmse =  14363.322503387162


In [33]:
# Setup and save Tree prediction

test_pred = model.predict(X_test.values) # Note that we need to feed our model the values or our dataframe X_test
predictions = np.c_[testId, test_pred] # Note that we take the argmax over the collumns to use our softmax output
submission = pd.DataFrame(predictions, columns = ['Id', 'SalePrice'])
submission['Id'] = submission['Id'].astype(int)
submission.to_csv("submissions/NNSubmission.csv", index=False)
submission.head()

Id      SalePrice
0  1461  115729.328125
1  1462  148874.625000
2  1463  154782.968750
3  1464  159385.453125
4  1465  170496.734375

In [34]:
# Import Ensemble prediction made from Tree/Forest models

Ensemble_prediction = pd.read_csv(os.path.join('submissions', 'EnsembleSubmission.csv'))

In [41]:
# Average old ensemble with NN model

Ensemble_prediction['NNSale'] = submission['SalePrice']
Ensemble_prediction['SalePrice'] = Ensemble_prediction[['SalePrice', 'NNSale']].mean(axis=1)
Ensemble_prediction = Ensemble_prediction.drop('NNSale', axis=1)

In [42]:
Ensemble_prediction.head()

Id      SalePrice
0  1461  120161.371094
1  1462  152452.843750
2  1463  162175.976562
3  1464  167157.189844
4  1465  174259.088281

In [43]:
Ensemble_prediction.to_csv('submissions/NNEnsembleSubmission.csv', index=False)